## Графовые нейронные сети

На этой практике будем решать задачу предсказания свободной энергии связывания для двух белковых молекул на основе структуры образованного ими белкового комплекса, а точнее — полноатомной структуры интерфейса взаимодействия.


Свободная энергия связывания: $\Delta G = RT \ln K_d$, где

- $R$ — универсальная газовая постоянная
- $T$ — температура
- $K_d = \frac{[R][L]}{[RL]}$ — константа диссоциации, равная отношению произведения концентраций белков R и L к концентрации их комплекса RL в равновесном состоянии

<style>
td, th {
   border: none!important;
}
</style>

|  |  |  |  |
| - | - | - | - |
| <img style="vertical-align:middle" src="../assets/images/4kro.png" width="250" alt="A grey image showing text 60 x 60"> | $\quad \longrightarrow \quad$ | <img style="vertical-align:middle" img src="../assets/images/4kro_sticks_contacts.png" width="200"> | $\longrightarrow \Delta G = RT \ln K_d$ |

План на сегодня:
- Построение графа из структуры белкового комплекса
- `torch-geometric`: упаковка графов в батчи
- `torch-geometric`: простая архитектура для задачи регрессии на графах

Нам понадобятся пакеты из стека `torch-geometric` для работы с графами, а также `plotly` для построения интерактивных графиков

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import sys
from pathlib import Path

import pandas as pd
import torch
from torch.optim import Adam
from torch_geometric.loader import DataLoader

sys.path.append(str(Path.cwd().parent))
from assets.utils.affinity_dataset import (
    ATOMS_INDICES,
    AffinityDataset,
    AtomicInterfaceGraphBuilder,
    DataItem,
    InterfaceGraph,
    PlotlyVis,
)

### Строим граф по атомной структуре

Наша задача: на основе структуры белкового комплекса предсказать свободную энергию связывания `dG`.

Мы будем использовать полноатомное представление структуры интерфейса, то есть узлами в нашем графе будут только те атомы, которые находятся не дальше чем 5 ангстрем от другого белка.
Для каждого атома мы знаем:
- тип атома: категориальная переменная, кодирующая химический элемент и его положение в аминокислоте
- тип аминокислоты: к какой из 20 аминокислот относится атом (тип атома даёт некоторую неоднозначность)
- положение атома в пространстве
- к какому из белков — рецептору или лиганду — относится атом

На основе межатомных расстояний будем строить граф следующим образом:
- для каждого атома интерфейса находим до `k` ближайших соседей в радиусе `r`
- опционально, если хотим построить двудольный граф, убираем все рёбра, соединяющие атомы одного белка

Мы будем работать с небольшим датасетом: всего 585 наблюдений в обучающей выборке и 150 в тестовой:

In [3]:
!cd ../assets/datasets/binding_affinity/ && tar -xzf pdb.tar.gz

In [4]:
dataset_dir = Path("../assets/datasets/binding_affinity/")
pdb_dir = dataset_dir / "pdb"
train_csv = pd.read_csv(dataset_dir / "affinity_train.csv")
train_csv.head()

uid receptor_chains ligand_chains     dG
0  1a22               B             A -12.91
1  1b27               A             D -19.09
2  1b6c               B             A  -8.94
3  1buh               A             B  -9.70
4  1dee               B             A  -8.72

### Строим граф по атомной структуре

In [5]:
record = train_csv.iloc[0]
item = DataItem(
    uid=record["uid"],
    receptor_chains=record["receptor_chains"],
    ligand_chains=record["ligand_chains"],
    dG=record["dG"],
    pdb=pdb_dir / f'{record["uid"]}.pdb',
)
graph_builder = AtomicInterfaceGraphBuilder(
    interface_distance=5.0, radius=5.0, keep_inner_edges=True
)
graph = graph_builder.build_graph(item)
graph

Data(edge_index=[2, 5174], y=-12.91, atoms=[333], residues=[333], coordinates=[333, 3], receptor_mask=[333], distances=[5174], num_nodes=333)

Глазами смотреть на такие данные совсем неудобно, давайте их визуализируем 

In [6]:
fig = PlotlyVis.create_figure(graph)
fig

Как из таких сложных объектов формировать батчи?

Будем формировать наш батч как огромный граф, где из матриц смежности исходных графов собрана блочно-диагональная матрица, а векторы-признаки просто конкатенируются вдоль размерности батча.

NB: конечно, в памяти мы будем хранить не огромную разреженную матрицу, а просто списки рёбер и ассоциированные с ними признаки

$$
\begin{split}\mathbf{A} = \begin{bmatrix} \mathbf{A}_1 & & \\ & \ddots & \\ & & \mathbf{A}_n \end{bmatrix}, \qquad \mathbf{X} = \begin{bmatrix} \mathbf{X}_1 \\ \vdots \\ \mathbf{X}_n \end{bmatrix}, \qquad \mathbf{Y} = \begin{bmatrix} \mathbf{Y}_1 \\ \vdots \\ \mathbf{Y}_n \end{bmatrix}.\end{split}
$$

### Датасет и загрузчик данных

In [7]:
train_dataset = AffinityDataset(
    datadir=pdb_dir,
    subset_csv=dataset_dir / "affinity_train.csv",
    graph_builder=graph_builder,
)
train_loader = DataLoader(train_dataset, batch_size=4, shuffle=True)

In [8]:
train_batch = next(iter(train_loader))
train_batch

DataBatch(edge_index=[2, 14560], y=[4], atoms=[977], residues=[977], coordinates=[977, 3], receptor_mask=[977], distances=[14560], num_nodes=977, batch=[977], ptr=[5])

В полученном батче лежат 4 исходных графа, теперь мы можем обрабатывать их параллельно, а когда нам потребуются операции для вершин внутри исходных графов (например, агрегация эмбеддингов вершин в эмбеддинг графа) — мы можем получить индексы исходных графов для всех вершин:

In [9]:
train_batch.batch

tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [10]:
train_batch.ptr

tensor([  0, 378, 512, 824, 977])

Объект класса `DataBatch` поддерживает тот же интерфейс, что и объекты, из которых мы его построили — значит, батч тоже можно визуализировать:

In [11]:
PlotlyVis.create_figure(train_batch)

### Строим графовую сеть

Архитектура для регрессии / классификации графов сводится к трём составляющим:
- получение эмбеддингов вершин через несколько раундов обмена сообщениями (обработка графовыми слоями)
  
  <!-- $h_i^{(t+1)} = h_i^{(t)} + \bigoplus_{j \in \mathcal{N}_i} f_{\theta}(h_i^{(t)}, h_j^{(t)})$ -->
  $h_i^{(t+1)} = \phi \left(h_i^{(t)}, \bigoplus_{j \in \mathcal{N}_i} \psi(h_i^{(t)}, h_j^{(t)})\right)$
- агрегация эмбеддингов вершин в эмбеддинг графа (readout layer)
  
  $h_\mathcal{V} = \bigoplus_{j \in \mathcal{V}} h_j^{(T)}$
- обучение регрессора / классификатора на графовом эмбеддинге
  
  $\hat{y} = \text{MLP}(h_\mathcal{V})$

Опишем архитектуру так, чтобы можно было использовать разные графовые слои:

In [12]:
from typing import Type

import torch.nn.functional as F
from torch import nn
from torch_geometric.nn.conv import GCNConv, GraphConv, MessagePassing
from torch_geometric.nn.pool import global_add_pool, global_max_pool, global_mean_pool


class GraphNet(nn.Module):
    def __init__(
        self,
        hidden_dim: int,
        graph_layer: Type[MessagePassing],
        n_layers: int,
        dropout: float = 0.5,
    ):
        super().__init__()
        # эмбеддинг для типов атомов
        self.embed = nn.Embedding(len(ATOMS_INDICES) + 1, hidden_dim)
        # список графовых слоёв
        self.conv = nn.ModuleList(
            [graph_layer(hidden_dim, hidden_dim) for _ in range(n_layers)]
        )
        # линейный слой для регрессии
        self.fc = nn.Linear(hidden_dim, 1)
        self.dropout = nn.Dropout(dropout, inplace=True)

    def forward(self, batch: InterfaceGraph):
        # 1. Эмбеддинги вершин
        x = self.embed(batch.atoms)
        for conv in self.conv:
            x = (x + conv(x, batch.edge_index)).relu()

        # 2. Эмбеддинг графа: усреднение по вершинам отдельных графов
        x = global_mean_pool(x, batch.batch)  # [batch_size, hidden_channels]

        # 3. Финальный регрессор поверх эмбеддинга графа
        x = self.dropout(x)
        x = self.fc(x)
        return x

Для первой модели возьмём самый простой графовый слой `GCNConv`:

$h_i^{(t+1)} = \mathbf{W}^{\top} \sum_{j \in
        \mathcal{N}(i) \cup \{ i \}} \frac{e_{j,i}}{\sqrt{\hat{d}_j
        \hat{d}_i}} h_j^{(t)}$

- $e_{j,i}$ — вес ребра между вершинами $i$ и $j$
- $\hat{d}_i$ — степень вершины $i$

In [13]:
model = GraphNet(hidden_dim=64, graph_layer=GCNConv, n_layers=3, dropout=0.1)
model.forward(train_batch)

tensor([[0.5389],
        [0.2023],
        [0.3691],
        [0.1753]], grad_fn=<AddmmBackward0>)

Попробуем обучить, считая корреляции Пирсона и Спирмена в качестве метрик:

In [14]:
from scipy.stats import pearsonr, spearmanr

test_dataset = AffinityDataset(
    datadir=pdb_dir,
    subset_csv=dataset_dir / "affinity_test.csv",
    graph_builder=graph_builder,
)

train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False)


@torch.no_grad()
def validate(loader: DataLoader, model: nn.Module) -> tuple[list[float], list[float]]:
    model.eval()
    ys = []
    yhats = []
    loss = 0.0
    for batch in loader:
        yhat = model.forward(batch)
        yhats.extend(yhat.flatten().tolist())
        ys.extend(batch.y.tolist())
        loss += F.mse_loss(yhat.flatten(), batch.y, reduction="sum").item()

    print(f"Loss: {loss / len(ys):.4f}, ", end="")
    print(f"MAE: {(torch.tensor(ys) - torch.tensor(yhats)).abs().mean():.4f}, ", end="")
    print(f"Pearson R: {pearsonr(ys, yhats).statistic:.4f}, ", end="")
    print(f"Spearman R: {spearmanr(ys, yhats).statistic:.4f}")
    model.train()
    return yhats, ys

In [15]:
torch.manual_seed(42)
model = GraphNet(hidden_dim=32, graph_layer=GCNConv, n_layers=3, dropout=0.1)
optim = Adam(model.parameters(), lr=0.001, weight_decay=1.0)

In [16]:
for i in range(50):
    model.train()
    for batch in train_loader:
        yhat = model.forward(batch)
        # loss = F.mse_loss(yhat.flatten(), batch.y)
        loss = F.huber_loss(yhat.flatten(), batch.y)
        loss.backward()
        optim.step()
        optim.zero_grad()

    if (i + 1) % 10 == 0:
        # validate(train_loader, model)
        validate(test_loader, model)

Loss: 8.1096, MAE: 2.2934, Pearson R: -0.2269, Spearman R: -0.2327
Loss: 4.5371, MAE: 1.6868, Pearson R: -0.1716, Spearman R: -0.1815
Loss: 4.4376, MAE: 1.6720, Pearson R: -0.1337, Spearman R: -0.1505
Loss: 4.0753, MAE: 1.6215, Pearson R: -0.1096, Spearman R: -0.1322
Loss: 4.2586, MAE: 1.6472, Pearson R: -0.0936, Spearman R: -0.1166


In [17]:
_ = validate(train_loader, model)

Loss: 5.1400, MAE: 1.7652, Pearson R: 0.0154, Spearman R: -0.0073


Результат не впечатляет: на тестовой выборке корреляция предсказаний с верными значениями отрицательная (да и, скорее всего, статистически незначимая), да и на обучающей выборке результат не очень.

Попробуем другой графовый слой `GraphConv`, более гибко агрегирующий информацию от соседей:

$h_i^{(t+1)} = \mathbf{W}_1 h_i^{(t)} + \mathbf{W}_2
        \sum_{j \in \mathcal{N}(i)} e_{j,i} \cdot h_j^{(t)}$

In [18]:
torch.manual_seed(42)
train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False)
model = GraphNet(hidden_dim=32, graph_layer=GraphConv, n_layers=3, dropout=0.1)
optim = Adam(model.parameters(), lr=0.001, weight_decay=1.0)

In [19]:
for i in range(50):
    for batch in train_loader:
        yhat = model.forward(batch)
        loss = F.mse_loss(yhat.flatten(), batch.y)
        # loss = F.huber_loss(yhat.flatten(), batch.affinity)
        loss.backward()
        optim.step()
        optim.zero_grad()

    if (i + 1) % 10 == 0:
        # validate(train_loader, model)
        validate(test_loader, model)

Loss: 5.9793, MAE: 1.9542, Pearson R: 0.1739, Spearman R: 0.1737
Loss: 4.7138, MAE: 1.7237, Pearson R: 0.2084, Spearman R: 0.1933
Loss: 4.5701, MAE: 1.6927, Pearson R: 0.1965, Spearman R: 0.1949
Loss: 4.3403, MAE: 1.6350, Pearson R: 0.2135, Spearman R: 0.2117
Loss: 5.5688, MAE: 1.8696, Pearson R: 0.2497, Spearman R: 0.2336


In [20]:
import plotly.express as px

yhat, ys = validate(test_loader, model)
px.scatter(x=yhat, y=ys)

Loss: 5.5688, MAE: 1.8696, Pearson R: 0.2497, Spearman R: 0.2336


### Изменения в графе

Посмотрим снова на наши данные.

Наши графы довольно большие, и в финальном слое, когда мы получаем эмбеддинг графа, мы делаем усреднение по большому числу вершин.

Можно ли уменьшить наши графы, сохранив только важные вершины для агрегации?

In [21]:
graph

Data(edge_index=[2, 5174], y=-12.91, atoms=[333], residues=[333], coordinates=[333, 3], receptor_mask=[333], distances=[5174], num_nodes=333)

In [22]:
PlotlyVis.create_figure(graph)

Идея следующая: что если оставить только рёбра между атомами, которые принадлежат разным белкам?

In [23]:
graph_builder = AtomicInterfaceGraphBuilder(
    interface_distance=5.0, radius=5.0, keep_inner_edges=False
)
interface_bigraph = graph_builder.build_graph(item)
print(interface_bigraph)
PlotlyVis.create_figure(interface_bigraph)

Data(edge_index=[2, 1532], y=-12.91, atoms=[333], residues=[333], coordinates=[333, 3], receptor_mask=[333], distances=[1532], num_nodes=333)


In [24]:
graph_builder = AtomicInterfaceGraphBuilder(
    interface_distance=5.0, radius=5.0, keep_inner_edges=False
)
train_dataset = AffinityDataset(
    datadir=pdb_dir,
    subset_csv=dataset_dir / "affinity_train.csv",
    graph_builder=graph_builder,
)
test_dataset = AffinityDataset(
    datadir=pdb_dir,
    subset_csv=dataset_dir / "affinity_test.csv",
    graph_builder=graph_builder,
)

train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False)

In [30]:
torch.manual_seed(42)
model = GraphNet(hidden_dim=32, graph_layer=GraphConv, n_layers=3, dropout=0.1)
optim = Adam(model.parameters(), lr=0.001, weight_decay=0.001)

In [31]:
for i in range(150):
    for batch in train_loader:
        yhat = model.forward(batch)
        loss = F.mse_loss(yhat.flatten(), batch.y)
        # loss = F.huber_loss(yhat.flatten(), batch.y)
        loss.backward()
        optim.step()
        optim.zero_grad()

    if (i + 1) % 10 == 0:
        validate(test_loader, model)

Loss: 5.4388, MAE: 1.8303, Pearson R: 0.1692, Spearman R: 0.1452
Loss: 3.7529, MAE: 1.5541, Pearson R: 0.2581, Spearman R: 0.2279
Loss: 3.7015, MAE: 1.5277, Pearson R: 0.3054, Spearman R: 0.2776
Loss: 3.7157, MAE: 1.5587, Pearson R: 0.2938, Spearman R: 0.2608
Loss: 3.6781, MAE: 1.5504, Pearson R: 0.3300, Spearman R: 0.2832
Loss: 3.4362, MAE: 1.4865, Pearson R: 0.3539, Spearman R: 0.3074
Loss: 3.4294, MAE: 1.4705, Pearson R: 0.3607, Spearman R: 0.3141
Loss: 3.4344, MAE: 1.4704, Pearson R: 0.3666, Spearman R: 0.3202
Loss: 3.5224, MAE: 1.4954, Pearson R: 0.3457, Spearman R: 0.3043
Loss: 4.0109, MAE: 1.5989, Pearson R: 0.3696, Spearman R: 0.3339
Loss: 3.6159, MAE: 1.4883, Pearson R: 0.3498, Spearman R: 0.3154
Loss: 3.7880, MAE: 1.5447, Pearson R: 0.3135, Spearman R: 0.2881
Loss: 4.2131, MAE: 1.6434, Pearson R: 0.3542, Spearman R: 0.3166
Loss: 3.9327, MAE: 1.5334, Pearson R: 0.3072, Spearman R: 0.2722
Loss: 3.9941, MAE: 1.5491, Pearson R: 0.3112, Spearman R: 0.2781


In [32]:
import plotly.express as px

yhat, ys = validate(test_loader, model)
px.scatter(x=yhat, y=ys)

Loss: 3.9941, MAE: 1.5491, Pearson R: 0.3112, Spearman R: 0.2781
